### Loading Required Libraries

In [87]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import warnings
warnings.filterwarnings('ignore')

In [88]:
confirmed_color = 'navy'
recovered_color = 'green'
death_color = 'indianred'
active_color = 'purple'

### Dateset Reference
**COVID-19 Data Repository by the Center for Systems Science and Engineering (CSSE) at Johns Hopkins University**
* https://github.com/CSSEGISandData/COVID-19

### Data Preparation

In [89]:
confirmed = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/'
                        'csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv')
death = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/'
                    'csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv')
recovered = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/'
                        'csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv')

In [90]:
del confirmed['Lat']
del confirmed['Long']
del confirmed['Province/State']
del death['Lat']
del death['Long']
del death['Province/State']
del recovered['Province/State']
del recovered['Lat']
del recovered['Long']
confirmed_agg = confirmed.groupby('Country/Region').sum()
recovered_agg = recovered.groupby('Country/Region').sum()
death_agg = death.groupby('Country/Region').sum()

In [91]:
tot_confirmed = pd.DataFrame(confirmed_agg[confirmed_agg.columns[-1]])
tot_recovered = pd.DataFrame(recovered_agg[recovered_agg.columns[-1]])
tot_death = pd.DataFrame(death_agg[death_agg.columns[-1]])

In [92]:
tot_confirmed.rename(columns={tot_confirmed.columns[-1]:'Confirmed_tot'},inplace=True)
tot_recovered.rename(columns={tot_recovered.columns[-1]:'Recovered_tot'},inplace=True)
tot_death.rename(columns={tot_death.columns[-1]:'Death_tot'},inplace=True)

In [93]:
country_wise_tot = tot_confirmed.join(tot_recovered,how='inner')
country_wise_tot = country_wise_tot.join(tot_death,how='inner')
country_wise_tot['Active_tot'] = country_wise_tot.Confirmed_tot-\
                                 country_wise_tot['Death_tot']-\
                                 country_wise_tot.Recovered_tot

In [94]:
#!pip install pycountry_convert

In [95]:
#Country name into continent
import pycountry_convert as pc
def country_to_continent(country_name):
    country_alpha2 = pc.country_name_to_country_alpha2(country_name)
    country_continent_code = pc.country_alpha2_to_continent_code(country_alpha2)
    country_continent_name = pc.convert_continent_code_to_continent_name(country_continent_code)
    return country_continent_name

l = {'Burma':'Asia','Myanmar':'Asia', 'Congo (Brazzaville)':'Africa','Congo (Kinshasa)':'Africa',
    "Cote d'Ivoire":'Africa','Diamond Princess':'Cruise Ship','Holy See':'Europe','Korea, South':'Asia',
    'Kosovo':'Europe','MS Zaandam':'Cruise Ship','Taiwan*':'Asia','Timor-Leste':'Asia',
    'US':'North America','West Bank and Gaza':'Asia','Western Sahara':'Africa','Taiwan':'Asia'}
lis = []
temp = []
for country in country_wise_tot.index.unique():
    try:
        continent = country_to_continent(country)
    except:
        try:
            continent = l[country]
        except:
            continent = float('NaN')
    #temp = [country,continent]
    temp = [continent,country]
    lis.append(temp)
df = pd.DataFrame(lis,columns={'Country/Region','Continent'})
df = df.set_index('Country/Region')
country_wise_tot = country_wise_tot.join(df,how='inner')
#country_wise_tot.head()

In [96]:
country_wise_tot['Recovered per 100 confirm'] = round(country_wise_tot['Recovered_tot']/country_wise_tot['Confirmed_tot']*100,2)
country_wise_tot['Death per 100 confirm'] = round(country_wise_tot.Death_tot/country_wise_tot.Confirmed_tot*100,2)
country_wise_tot['Active per 100 confirm'] = round(country_wise_tot.Active_tot/country_wise_tot.Confirmed_tot*100,2)
#country_wise_tot.head()

In [97]:
day_wise_confirmed = pd.DataFrame(confirmed_agg.sum(),columns={'Confirmed_dw'})
day_wise_recovered = pd.DataFrame(recovered_agg.sum(),columns={'Recovered_dw'})
day_wise_death = pd.DataFrame(death_agg.sum(),columns={'Death_dw'})
day_wise = day_wise_confirmed.join(day_wise_recovered,how='inner')
day_wise = day_wise.join(day_wise_death,how='inner')
day_wise['Active_dw'] = day_wise.Confirmed_dw-day_wise.Recovered_dw-day_wise.Death_dw
#day_wise.tail()

In [98]:
l = []
for i in confirmed_agg.columns:
    for j in confirmed_agg.index:
        l.append([i,j,confirmed_agg.loc[j,i],recovered_agg.loc[j,i],death_agg.loc[j,i]])
        time_series = pd.DataFrame(l,columns={'Date','Country/Region','Confirmed','Recovered','Death'})                        
time_series.tail()

Country/Region               Death  Date  Confirmed  Recovered
28759        6/22/20  West Bank and Gaza  1001        442          3
28760        6/22/20      Western Sahara    10          8          1
28761        6/22/20               Yemen   967        350        257
28762        6/22/20              Zambia  1430       1194         11
28763        6/22/20            Zimbabwe   512         64          6

In [99]:
time_series.rename(columns={'Death':'Country/Region','Recovered':'Death',
                            'Country/Region':'Date','Confirmed':'Recovered',
                            'Date':'Confirmed'},inplace=True)
time_series.head()

Date Country/Region  Confirmed  Recovered  Death
0  1/22/20    Afghanistan          0          0      0
1  1/22/20        Albania          0          0      0
2  1/22/20        Algeria          0          0      0
3  1/22/20        Andorra          0          0      0
4  1/22/20         Angola          0          0      0

In [101]:
time_series['Active'] = time_series.Confirmed-time_series.Recovered-time_series.Death
time_series.set_index('Date',inplace=True)
#time_series.tail()

In [102]:
time_series_dw = time_series.join(day_wise[['Confirmed_dw','Recovered_dw','Death_dw','Active_dw']],how='inner')
#time_series_dw.head()

In [103]:
time_series_dw['Confirmed%'] = round(time_series_dw.Confirmed/time_series_dw.Confirmed_dw*100,1)
time_series_dw['Recovered%'] = round(time_series_dw.Recovered/time_series_dw.Recovered_dw*100,1)
time_series_dw['Death%'] = round(time_series_dw.Death/time_series_dw.Death_dw*100,1)
time_series_dw['Active%'] = round(time_series_dw.Active/time_series_dw.Active_dw*100,1)
#time_series_dw.head()

## Total cases till now

In [106]:
temp = pd.DataFrame(country_wise_tot[['Confirmed_tot','Recovered_tot','Death_tot','Active_tot']].sum()).T
temp = temp.melt(value_vars=['Confirmed_tot','Recovered_tot','Death_tot','Active_tot'])
fig = px.treemap(temp, path=["variable"], values="value", height=250, 
                 color_discrete_sequence=[confirmed_color, recovered_color,active_color,death_color])
fig.data[0].textinfo = 'label+text+value'
fig.show()

## Global Cases Distribution

In [107]:
fig = px.choropleth(country_wise_tot, locations=country_wise_tot.index, locationmode='country names', 
                  color='Confirmed_tot', hover_name=country_wise_tot.index, 
                  title='Confirmed', hover_data=['Confirmed_tot'], color_continuous_scale='Blues')
fig.show()

In [108]:
fig = px.choropleth(country_wise_tot, locations=country_wise_tot.index, locationmode='country names', 
                  color='Recovered_tot', hover_name=country_wise_tot.index, 
                  title='Recovered', hover_data=['Recovered_tot'], color_continuous_scale='Greens')
fig.show()

In [109]:
fig = px.choropleth(country_wise_tot, locations=country_wise_tot.index, locationmode='country names', 
                  color='Active_tot', hover_name=country_wise_tot.index, 
                  title='Active', hover_data=['Active_tot'], color_continuous_scale='Purp')
#fig.update_layout(coloraxis_showscale=False)
fig.show()

In [110]:
fig = px.choropleth(country_wise_tot, locations=country_wise_tot.index, locationmode='country names', 
                  color='Death_tot', hover_name=country_wise_tot.index, 
                  title='Death', hover_data=['Death_tot'], color_continuous_scale='Reds')
fig.show()

## Commulative Day-Wise Global Cases

In [111]:
fig = px.bar(day_wise, x=day_wise.index, y='Confirmed_dw', width=1500, color_discrete_sequence=[confirmed_color],template='simple_white')
fig.update_layout(title='Confirmed', xaxis_title="Date", yaxis_title="No. of Confirmed Cases")
fig.show()

In [112]:
fig = px.bar(day_wise, x=day_wise.index, y='Recovered_dw', width=1500, color_discrete_sequence=[recovered_color],template='simple_white')
fig.update_layout(title='Recovered', xaxis_title="Date", yaxis_title="No. of Recovered Cases")
fig.show()

In [113]:
fig = px.bar(day_wise, x=day_wise.index, y='Active_dw', width=1500, color_discrete_sequence=[active_color],template='simple_white')
fig.update_layout(title='Active', xaxis_title="Date", yaxis_title="No. of Active Cases")
fig.show()

In [114]:
fig = px.bar(day_wise, x=day_wise.index, y='Death_dw', width=1500, color_discrete_sequence=[death_color],template='simple_white')
fig.update_layout(title='Death', xaxis_title="Date", yaxis_title="No. of Death Cases")
fig.show()

In [115]:
fig = px.line(day_wise, x=day_wise.index, y='Confirmed_dw', width=1500, color_discrete_sequence=[confirmed_color],
              hover_name='Confirmed_dw',template='simple_white')
fig.add_scatter(x= day_wise.index,y=day_wise['Recovered_dw'],name='Recovered',marker={'color': recovered_color,'opacity': 0.6,'colorscale': 'Viridis'},)
fig.add_scatter(x=day_wise.index,y=day_wise.Active_dw,name='Active',marker={'color': active_color,'opacity': 0.6,'colorscale': 'Viridis'})
fig.add_scatter(x=day_wise.index,y=day_wise.Death_dw,name='Death',marker={'color': death_color,'opacity': 0.6,'colorscale': 'Viridis'})
fig.update_layout(title='Day Wise Analysis', xaxis_title="Date", yaxis_title="No. of Cases")
fig.show()


## Percentage wise daily distribution

In [116]:
fig = px.bar(time_series_dw, x=pd.to_datetime(time_series_dw.index), y='Confirmed%', color='Country/Region', 
             range_y=(0, 100), title='Confirmed', 
             color_discrete_sequence=px.colors.qualitative.Plotly)
fig.show()

In [117]:
fig = px.bar(time_series_dw, x=pd.to_datetime(time_series_dw.index), y='Recovered%', color='Country/Region', 
             range_y=(0, 100), title='Recovered', 
             color_discrete_sequence=px.colors.qualitative.Plotly)
fig.show()

In [118]:
fig = px.bar(time_series_dw, x=pd.to_datetime(time_series_dw.index), y='Active%', color='Country/Region', 
             range_y=(0, 100), title='Active', 
             color_discrete_sequence=px.colors.qualitative.Plotly)
fig.show()

In [119]:
fig = px.bar(time_series_dw, x=pd.to_datetime(time_series_dw.index), y='Death%', color='Country/Region', 
             range_y=(0, 100), title='Death', 
             color_discrete_sequence=px.colors.qualitative.Plotly)
fig.show()

# Top21 Countries Affected

In [120]:
temp = country_wise_tot.sort_values('Confirmed_tot').tail(21)
fig = go.Figure(data=[
    go.Bar(name='Death', y=temp.head(21).index, x=temp['Death_tot'].head(21),orientation='h',marker_color=death_color),
    go.Bar(name='Recovered', y=temp.head(21).index, x=temp['Recovered_tot'].head(21),orientation='h',marker_color=recovered_color),
    go.Bar(name='Confirmed', y=temp.head(21).index, x=temp['Confirmed_tot'].head(21),orientation='h',marker_color=confirmed_color)
])
fig.update_layout(barmode='stack',title='Top21 Confirmed/Recovered/Death Stacked', xaxis_title="Cases", yaxis_title="Country", 
                      yaxis_categoryorder = 'total ascending',
                      uniformtext_minsize=8, uniformtext_mode='hide',template='simple_white')
fig.show()

In [121]:
fig = px.bar(country_wise_tot.sort_values('Active_tot').tail(21), 
                 x='Active_tot', y=country_wise_tot.sort_values('Active_tot').tail(21).index, 
                 color='Continent',color_continuous_scale='Blues',
                 text='Active_tot', orientation='h', width=1500, 
                 color_discrete_sequence = px.colors.qualitative.T10, 
                 template='simple_white')
fig.update_layout(title='Top21 Active', xaxis_title="", yaxis_title="", 
                      yaxis_categoryorder = 'total ascending',
                      uniformtext_minsize=8, uniformtext_mode='hide')
fig.show()

In [122]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=temp['Death per 100 confirm'], x=temp.index,
                    mode='lines+markers',
                    name='Death/100 Confirmed',marker_color=death_color))
fig.add_trace(go.Scatter(y=temp['Recovered per 100 confirm'], x=temp.index,
                    mode='lines+markers',
                    name='Recovered/100 Confirmed',marker_color=recovered_color))
fig.add_trace(go.Scatter(y=temp['Active per 100 confirm'], x=temp.index,
                    mode='lines+markers', name='Active/100 Confirmed',marker_color=active_color))
fig.update_layout(height=700, title_text="Top21 Cases per 100 Confirmed",template='simple_white')
fig.show()

## Top21 Confirmed Cases Distribution - Day wise

In [123]:
from plotly.offline import iplot, init_notebook_mode
init_notebook_mode(connected = True)
top21=country_wise_tot.sort_values('Confirmed_tot').tail(21).index
fig = make_subplots(rows=7, cols=3, shared_xaxes=False)
n = 0
for row in range(1,8):
    for col in range(1,4):
        fig.add_trace(go.Bar(x = pd.to_datetime(time_series_dw.index.unique()),
        y = time_series_dw.loc[time_series_dw['Country/Region']==top21[n], 'Confirmed'],name=top21[n]),
              row, col)
        n+=1
fig.update_layout(height=3000, title_text="Confirmed cases of top21",template='simple_white')
fig.show()

In [124]:
top21_confirmed_new = pd.DataFrame(confirmed_agg.loc[top21[0]].diff())
top21_recovered_new = pd.DataFrame(recovered_agg.loc[top21[0]].diff())
top21_death_new = pd.DataFrame(death_agg.loc[top21[0]].diff())
for i,country in enumerate(top21):
    top21_confirmed_new[country] = confirmed_agg.loc[country].diff()
    top21_recovered_new[country] = recovered_agg.loc[country].diff()
    top21_death_new[country] = death_agg.loc[country].diff()
#top21_death_new

### Top21 - New Cases Daily Confirmed

In [125]:
fig = go.Figure()
for i in top21_confirmed_new:
    fig.add_trace(go.Scatter(y=top21_confirmed_new[i], x=top21_confirmed_new.index,
                    mode='lines+markers',
                    name=i))
fig.update_layout(height=700, title_text="Top21 New Number of Confirmed Cases corresponding to previous day",template='simple_white')
fig.show()

In [126]:
fig = go.Figure()
for i in top21_recovered_new:
    fig.add_trace(go.Scatter(y=top21_recovered_new[i], x=top21_recovered_new.index,
                    mode='lines+markers',
                    name=i))
fig.update_layout(height=700, title_text="Top21 New Number of Recovered Cases corresponding to previous day",template='simple_white')
fig.show()

In [127]:
fig = go.Figure()
for i in top21_death_new:
    fig.add_trace(go.Scatter(y=top21_death_new[i], x=top21_death_new.index,
                    mode='lines+markers',
                    name=i))
fig.update_layout(height=700, title_text="Top21 New Number of Death Cases corresponding to previous day",template='simple_white')
fig.show()

## Continent Wise Cases Distribution

In [128]:
fig = px.sunburst(country_wise_tot, path=['Continent',country_wise_tot.index],
                    values='Confirmed_tot', color='Continent',
                    hover_data=["Confirmed_tot", "Recovered_tot",'Death_tot' ]
                    )
fig.update_layout(height=1000, title_text="Confirmed")
fig.show()

In [129]:
fig = px.sunburst(country_wise_tot, path=['Continent',country_wise_tot.index],
                    values='Recovered_tot', color='Continent',
                    hover_data=["Confirmed_tot", "Recovered_tot",'Death_tot' ]
                    )
fig.update_layout(height=1000, title_text="Recovered")
fig.show()

In [130]:
fig = px.sunburst(country_wise_tot, path=['Continent',country_wise_tot.index],
                    values='Active_tot', color='Continent',
                    hover_data=["Confirmed_tot", "Recovered_tot",'Death_tot' ]
                    )
fig.update_layout(height=1000, title_text="Active")
fig.show()

In [131]:
fig = px.sunburst(country_wise_tot, path=['Continent',country_wise_tot.index],
                    values='Death_tot', color='Continent',
                    hover_data=["Confirmed_tot", "Recovered_tot",'Death_tot' ]
                    )
fig.update_layout(height=1000, title_text="Death")
fig.show()

Please upvote if you like it and don't forget to suggest some changes I can make or can add new things😋